#####/Volumes/bigdata/ecommerce_clientes/ecommerce/ecommerce_customer_data_large.csv

In [0]:
%sql
-- 1. CREAR EL CATÁLOGO (Contenedor principal)
CREATE CATALOG IF NOT EXISTS bigdata; 

-- 2. CREAR EL ESQUEMA (Base de Datos)
CREATE SCHEMA IF NOT EXISTS bigdata.ecommerce_clientes; 

-- 3. USAR EL ESQUEMA
USE bigdata.ecommerce_clientes;

In [0]:
%sql
-- 1. Borramos la tabla para empezar limpios y evitar "basura" de intentos fallidos
DROP TABLE IF EXISTS bigdata.ecommerce_clientes.dim_cliente;

-- 2. Creamos la tabla con la estructura correcta (incluyendo las columnas que faltaban)
CREATE TABLE bigdata.ecommerce_clientes.dim_cliente (
    Customer_ID           BIGINT          NOT NULL COMMENT 'PK',
    Purchase_Date         TIMESTAMP       NOT NULL COMMENT 'Usamos TIMESTAMP por la hora',
    Product_Category      STRING,
    Product_Price         DECIMAL(10,2),
    Quantity              BIGINT          COMMENT 'Cambiado a BIGINT para coincidir con el CSV',
    Total_Purchase_Amount DECIMAL(10,2),
    Payment_Method        STRING,
    Customer_Age          INT             COMMENT 'Mapeado desde Customer Age',
    Returns               DOUBLE          COMMENT 'Mapeado desde Returns',
    Customer_Name         STRING,
    Age                   INT,
    Gender                STRING,
    Churn                 INT             COMMENT 'Cargamos como INT (0/1)'
)
USING delta;

-- 3. Cargamos los datos con transformación explícita (Casteo y Renombrado)
COPY INTO bigdata.ecommerce_clientes.dim_cliente
FROM (
  SELECT 
    `Customer ID`::BIGINT          AS Customer_ID,
    `Purchase Date`::TIMESTAMP     AS Purchase_Date,
    `Product Category`             AS Product_Category,
    `Product Price`::DECIMAL(10,2) AS Product_Price,
    Quantity::BIGINT               AS Quantity,        -- Aquí solucionamos el error de tipos
    `Total Purchase Amount`::DECIMAL(10,2) AS Total_Purchase_Amount,
    `Payment Method`               AS Payment_Method,
    `Customer Age`::INT            AS Customer_Age,    -- Aquí arreglamos el nombre con espacio
    Returns::DOUBLE                AS Returns,
    `Customer Name`                AS Customer_Name,
    Age::INT                       AS Age,
    Gender                         AS Gender,
    Churn::INT                     AS Churn
  FROM '/Volumes/bigdata/ecommerce_clientes/ecommerce/ecommerce_customer_data_large.csv'
)
FILEFORMAT = CSV
FORMAT_OPTIONS (
  'header' = 'true',        -- Leemos el header para poder usar los nombres en el SELECT
  'delimiter' = ',',
  'inferSchema' = 'false'   -- No inferimos, nosotros controlamos los tipos arriba
);

num_affected_rows num_inserted_rows num_skipped_corrupt_files 250000 250000 0

In [0]:
%sql
SHOW CREATE TABLE bigdata.ecommerce_clientes.dim_cliente;

createtab_stmt CREATE TABLE bigdata.ecommerce_clientes.dim_cliente (
 Customer_ID BIGINT NOT NULL COMMENT 'PK',
 Purchase_Date TIMESTAMP NOT NULL COMMENT 'Usamos TIMESTAMP por la hora',
 Product_Category STRING,
 Product_Price DECIMAL(10,2),
 Quantity BIGINT COMMENT 'Cambiado a BIGINT para coincidir con el CSV',
 Total_Purchase_Amount DECIMAL(10,2),
 Payment_Method STRING,
 Customer_Age INT COMMENT 'Mapeado desde Customer Age',
 Returns DOUBLE COMMENT 'Mapeado desde Returns',
 Customer_Name STRING,
 Age INT,
 Gender STRING,
 Churn INT COMMENT 'Cargamos como INT (0/1)')
USING delta
COLLATION 'UTF8_BINARY'
TBLPROPERTIES (
 'delta.enableDeletionVectors' = 'true',
 'delta.enableRowTracking' = 'true',
 'delta.feature.appendOnly' = 'supported',
 'delta.feature.deletionVectors' = 'supported',
 'delta.feature.domainMetadata' = 'supported',
 'delta.feature.invariants' = 'supported',
 'delta.feature.rowTracking' = 'supported',
 'delta.minReaderVersion' = '3',
 'delta.minWriterVersion' = '7',
 'delta.parquet.compression.codec' = 'zstd')

In [0]:
%sql
DESCRIBE TABLE bigdata.ecommerce_clientes.dim_cliente;

col_name data_type comment Customer_ID bigint PK Purchase_Date timestamp Usamos TIMESTAMP por la hora Product_Category string null Product_Price decimal(10,2) null Quantity bigint Cambiado a BIGINT para coincidir con el CSV Total_Purchase_Amount decimal(10,2) null Payment_Method string null Customer_Age int Mapeado desde Customer Age Returns double Mapeado desde Returns Customer_Name string null Age int null Gender string null Churn int Cargamos como INT (0/1)

In [0]:
%sql
SELECT * FROM bigdata.ecommerce_clientes.dim_cliente
LIMIT 5

Customer_ID Purchase_Date Product_Category Product_Price Quantity Total_Purchase_Amount Payment_Method Customer_Age Returns Customer_Name Age Gender Churn 44605 2023-05-03T21:30:02.000Z Home 177.00 1 2427.00 PayPal 31 1.0 John Rivera 31 Female 0 44605 2021-05-16T13:57:44.000Z Electronics 174.00 3 2448.00 PayPal 31 1.0 John Rivera 31 Female 0 44605 2020-07-13T06:16:57.000Z Books 413.00 1 2345.00 Credit Card 31 1.0 John Rivera 31 Female 0 44605 2023-01-17T13:14:36.000Z Electronics 396.00 3 937.00 Cash 31 0.0 John Rivera 31 Female 0 44605 2021-05-01T11:29:27.000Z Books 259.00 4 2598.00 PayPal 31 1.0 John Rivera 31 Female 0

In [0]:
%sql
SELECT count(*) FROM bigdata.ecommerce_clientes.dim_cliente

count(*) 250000

In [0]:
%sql
SELECT * FROM bigdata.ecommerce_clientes.dim_cliente where Product_Category = 'Electronics';

Customer_ID Purchase_Date Product_Category Product_Price Quantity Total_Purchase_Amount Payment_Method Customer_Age Returns Customer_Name Age Gender Churn 44605 2021-05-16T13:57:44.000Z Electronics 174.00 3 2448.00 PayPal 31 1.0 John Rivera 31 Female 0 44605 2023-01-17T13:14:36.000Z Electronics 396.00 3 937.00 Cash 31 0.0 John Rivera 31 Female 0 13738 2023-07-25T05:17:24.000Z Electronics 205.00 1 2773.00 Credit Card 27 null Lauren Johnson 27 Female 0 13738 2023-02-09T00:53:14.000Z Electronics 40.00 4 4327.00 Cash 27 0.0 Lauren Johnson 27 Female 0 33969 2021-12-20T23:44:57.000Z Electronics 428.00 4 2289.00 Cash 27 0.0 Carol Allen 27 Male 0 42650 2022-03-18T13:52:08.000Z Electronics 256.00 2 3548.00 Credit Card 20 0.0 Curtis Smith 20 Female 0 42650 2022-01-26T12:50:30.000Z Electronics 105.00 2 3721.00 Credit Card 20 null Curtis Smith 20 Female 0 42650 2020-11-11T07:19:18.000Z Electronics 193.00 2 3266.00 PayPal 20 1.0 Curtis Smith 20 Female 0 42650 2021-08-01T05:27:13.000Z Electronics 30.00 3 5024.00 Credit Card 20 1.0 Curtis Smith 20 Female 0 42650 2020-05-24T06:45:48.000Z Electronics 307.00 3 973.00 PayPal 20 null Curtis Smith 20 Female 0 42650 2022-03-24T00:05:26.000Z Electronics 254.00 1 3865.00 PayPal 20 0.0 Curtis Smith 20 Female 0 24053 2020-11-17T13:14:27.000Z Electronics 102.00 2 5206.00 Credit Card 53 1.0 Jose Green 53 Male 0 24053 2020-07-05T06:30:39.000Z Electronics 364.00 3 1008.00 Credit Card 53 0.0 Jose Green 53 Male 0 19676 2021-06-26T23:49:18.000Z Electronics 329.00 1 3391.00 Cash 57 1.0 Linda Lee 57 Male 0 19676 2020-04-20T14:08:25.000Z Electronics 165.00 5 603.00 Credit Card 57 0.0 Linda Lee 57 Male 0 19676 2021-03-23T17:36:30.000Z Electronics 218.00 4 2866.00 PayPal 57 null Linda Lee 57 Male 0 19917 2022-10-18T22:58:32.000Z Electronics 41.00 2 743.00 Cash 34 null Joshua Davis 34 Male 1 23734 2022-09-21T19:10:37.000Z Electronics 75.00 1 289.00 PayPal 18 0.0 Cheryl Espinoza 18 Male 0 16921 2021-04-22T22:10:06.000Z Electronics 500.00 2 988.00 Cash 54 1.0 Cheyenne James 54 Male 0 7796 2022-10-22T12:12:29.000Z Electronics 145.00 2 2134.00 PayPal 21 0.0 Lisa Dennis 21 Male 0 21035 2022-09-03T16:41:38.000Z Electronics 443.00 2 1884.00 Credit Card 50 1.0 Peter Watson 50 Female 1 21035 2021-06-15T06:53:41.000Z Electronics 116.00 3 2334.00 Credit Card 50 0.0 Peter Watson 50 Female 1 21035 2021-01-27T18:26:00.000Z Electronics 457.00 2 2919.00 PayPal 50 1.0 Peter Watson 50 Female 1 37125 2021-06-08T15:13:38.000Z Electronics 207.00 5 783.00 Credit Card 24 null Terry Campos 24 Female 0 37125 2022-08-23T18:10:45.000Z Electronics 311.00 2 2992.00 Cash 24 0.0 Terry Campos 24 Female 0 41840 2021-05-10T15:05:57.000Z Electronics 298.00 3 1837.00 Cash 48 1.0 Ronald Berger 48 Male 0 41840 2022-09-11T22:15:13.000Z Electronics 251.00 3 2525.00 PayPal 48 0.0 Ronald Berger 48 Male 0 41840 2021-11-12T13:57:32.000Z Electronics 277.00 5 3975.00 PayPal 48 0.0 Ronald Berger 48 Male 0 13389 2022-07-14T10:10:33.000Z Electronics 222.00 2 1731.00 Cash 51 null Monica Ramos 51 Male 0 24473 2020-05-29T23:54:54.000Z Electronics 474.00 3 4609.00 PayPal 38 0.0 Nicole Lewis 38 Female 0 11230 2021-04-21T17:47:10.000Z Electronics 296.00 5 2232.00 PayPal 23 1.0 Rebecca Boyer 23 Male 0 24741 2022-06-05T02:09:39.000Z Electronics 87.00 4 688.00 Cash 50 1.0 Steven Mcmillan 50 Female 0 24741 2022-10-08T19:22:53.000Z Electronics 230.00 3 2080.00 PayPal 50 null Steven Mcmillan 50 Female 0 10191 2022-02-19T19:43:15.000Z Electronics 229.00 5 3553.00 PayPal 66 1.0 Walter Griffin 66 Male 0 10191 2021-12-20T15:38:20.000Z Electronics 118.00 2 2304.00 Credit Card 66 1.0 Walter Griffin 66 Male 0 10191 2021-06-01T15:17:24.000Z Electronics 76.00 1 3306.00 Credit Card 66 1.0 Walter Griffin 66 Male 0 10191 2021-08-31T18:50:02.000Z Electronics 157.00 1 4382.00 Credit Card 66 null Walter Griffin 66 Male 0 18467 2023-05-09T02:20:01.000Z Electronics 92.00 4 3660.00 PayPal 23 0.0 Terri Carter 23 Male 0 34857 2023-02-06T19:10:18.000Z Electronics 284.00 4 402.00 PayPal 57 0.0 Al

In [0]:
%sql
SELECT Product_Category, count(*) AS total FROM bigdata.ecommerce_clientes.dim_cliente GROUP BY Product_Category HAVING Product_Category = 'Electronics';

Product_Category total Electronics 62630